# Set up imports

In [1]:
# setting up our imports
import re, string, unicodedata
import numpy as np
import pandas as pd
from pprint import pprint
import nltk
from nltk.corpus import stopwords
nltk.download('stopwords')
stop_words = stopwords.words('english')

# Gensim
import gensim
import gensim.corpora as corpora
from gensim.utils import simple_preprocess
from gensim.models import CoherenceModel
from gensim.models import LdaModel, LdaMulticore
import gensim.downloader as api
from gensim.models import LsiModel
from gensim.models import ldaseqmodel
from gensim.corpora import Dictionary, bleicorpus
from gensim.matutils import hellinger

nltk.download('wordnet')
from nltk.stem.porter import PorterStemmer
from nltk.stem.wordnet import WordNetLemmatizer
#from bs4 import BeautifulSoup
#from nltk import word_tokenize, sent_tokenize

# Plotting tools 
import pyLDAvis
import pyLDAvis.gensim  # don't skip this
import matplotlib.pyplot as plt
# %matplotlib inline

# Enable logging for gensim - optional
#import logging
#logging.basicConfig(format='%(asctime)s : %(levelname)s : %(message)s', level=logging.ERROR)
#logging.root.setLevel(level=logging.INFO)
#import warnings
#warnings.filterwarnings("ignore",category=DeprecationWarning)

[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\Kornelius\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\utils.py:1197: UserWarning: detected Windows; aliasing chunkize to chunkize_serial
  warnings.warn("detected Windows; aliasing chunkize to chunkize_serial")
[nltk_data] Downloading package wordnet to
[nltk_data]     C:\Users\Kornelius\AppData\Roaming\nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


# load dataset

In [2]:
# Load dataset
df = pd.read_csv('C:/Users/Kornelius/Desktop/Data 2/nips-papers/papers.csv', header = 0, sep = ';', error_bad_lines=False)
# Drop the columns not needed
df = df.drop(columns=['id', 'event_type', 'pdf_name'], axis=1)

In [3]:
# Drop a row by condition
df = df[df.abstract != 'Abstract Missing']

In [4]:
# sort by year
df = df.sort_values(by=['year'])
df

year                                              title  \
6389  1997        A Neural Network Based Head Tracking System   
5909  1997  Learning Generative Models with the Up Propaga...   
4884  2000   Algorithms for Non-negative Matrix Factorization   
5281  2001  Characterizing Neural Gain Control using Spike...   
4471  2007  Learning Horizontal Connections in a Sparse Co...   
4477  2007                 Predictive Matrix-Variate t Models   
4480  2007                        Competition Adds Complexity   
6095  2007  Progressive mixture rules are deviation subopt...   
6085  2007  Adaptive Embedded Subgraph Algorithms using Wa...   
3564  2007  Estimating disparity with confidence from ener...   
3430  2007          Discriminative Batch Mode Active Learning   
6000  2007   Random Sampling of States in Dynamic Programming   
4515  2007        Mining Internet-Scale Software Repositories   
3434  2007                Computing Robust Counter-Strategies   
5958  2007           The Infinite Gamma-Poisson Feature Model   
4607  2007  Linear programming analysis of loopy belief pr...   
6031  2007  Fitted Q-iteration in continuous action-space ...   
6202  2007  Efficient Convex Relaxation for Transductive S...   
4439  2007  An online Hebbian learning rule that performs ...   
4385  2007  On Ranking in Survival Analysis: Bounds on the...   
6255  2007  The Noisy-Logical Distribution and its Applica...   
4363  2007  Support Vector Machine Classification with Ind...   
3565  2007  Modelling motion primitives and their timing i...   
6271  2007  Modeling image patches with a directed hierarc...   
4276  2007  Gaussian Process Models for Link Analysis and ...   
4226  2007                Spatial Latent Dirichlet Allocation   
6405  2007  Regulator Discovery from Gene Expression Time ...   
6479  2007                            Supervised Topic Models   
3578  2007  EEG-Based Brain-Computer Interaction: Improved...   
6549  2007  A General Boosting Method and its Application ...   
...    ...                                                ...   
5371  2017         Independence clustering (without a matrix)   
5370  2017  Interpretable and Globally Optimal Prediction ...   
5383  2017  From Parity to Preference-based Notions of Fai...   
5368  2017  On Tensor Train Rank Minimization : Statistica...   
5358  2017  Gradients of Generative Models for Improved Di...   
5357  2017  Dual-Agent GANs for Photorealistic and Identit...   
5351  2017  Query Complexity of Clustering with Side Infor...   
3484  2017                       Welfare Guarantees from Data   
5337  2017  Subset Selection and Summarization in Sequenti...   
5327  2017  Clustering Billions of Reads for DNA Data Storage   
5360  2017  Expectation Propagation with Stochastic Kineti...   
5521  2017     Model evidence from nonequilibrium simulations   
5401  2017                Collecting Telemetry Data Privately   
5421  2017  Learning Combinatorial Optimization Algorithms...   
5506  2017  k-Support and Ordered Weighted Sparsity for Ov...   
5501  2017     From Bayesian Sparsity to Gated Recurrent Nets   
5498  2017  Minimax Estimation of Bandable Precision Matrices   
5492  2017  Lower bounds on the robustness to adversarial ...   
5488  2017  Union of Intersections (UoI) for Interpretable...   
5484  2017  Uprooting and Rerooting Higher-Order Graphical...   
5411  2017  When Cyclic Coordinate Descent Outperforms Ran...   
5465  2017  InfoGAIL: Interpretable Imitation Learning fro...   
5450  2017  The Expressive Power of Neural Networks: A Vie...   
5446  2017       Improving the Expected Improvement Algorithm   
5444  2017  Clustering Stable Instances of Euclidean k-means.   
5440  2017  Deliberation Networks: Sequence Generation Bey...   
5436  2017  On the Model Shrinkage Effect of Gamma Process...   
5434  2017      Regret Analysis for Continuous Dueling Bandit   
5459  2017  Identification of Gaussian Process State Space...   
5278  2017                    Hierarchica

In [5]:
df.year.value_counts()

2017    679
2016    569
2014    411
2015    403
2013    360
2012    342
2011    290
2010    288
2009    257
2008    222
2007     99
1997      2
2001      1
2000      1
Name: year, dtype: int64

In [6]:
data = df.abstract.values.tolist()

In [7]:
from nltk.corpus import stopwords 
from nltk.stem.wordnet import WordNetLemmatizer
import string
stop = set(stopwords.words('english'))
exclude = set(string.punctuation) 
lemma = WordNetLemmatizer()
def clean(data):
    stop_free = " ".join([i for i in data.lower().split() if i not in stop])
    punc_free = ''.join(ch for ch in stop_free if ch not in exclude)
    normalized = " ".join(lemma.lemmatize(word) for word in punc_free.split())
    return normalized

data = [clean(data).split() for data in data]  

In [8]:
# remove characters and numbers
def sent_to_words(sentences):
    for sentence in sentences:
        yield(gensim.utils.simple_preprocess(str(sentence), deacc=True))  # deacc=True removes punctuations

data_words = list(sent_to_words(data))

In [9]:
data = data_words
# Create Dictionary
id2word = corpora.Dictionary(data)
print((id2word))

Dictionary(16129 unique tokens: ['adaptation', 'adjusts', 'allows', 'also', 'auxiliary']...)


In [10]:
# Create Corpus
texts = data
# Term Document Frequency and creating corpus
corpus = [id2word.doc2bow(text) for text in texts]

In [11]:
from gensim.models import ldaseqmodel
import numpy
from gensim.matutils import hellinger

In [12]:
time_slice = [2 , 1, 1, 99, 222, 257, 288, 290, 342, 360, 411, 403, 569, 679]

In [13]:
#ldaseq = ldaseqmodel.LdaSeqModel(corpus=corpus, id2word=id2word, time_slice=time_slice, num_topics=5)

ldaseq = ldaseqmodel.LdaSeqModel(corpus=corpus , id2word=id2word , num_topics=10, time_slice=time_slice)

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

...

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldaseqmodel.py:230: RuntimeWarning: divide by zero encountered in double_scalars
  convergence = np.fabs((bound - old_bound) / old_bound)


In [14]:
#ldaseq.print_topics(time=0) # at timeslice 1, those are the topics, word probability to the right 

In [15]:
ldaseq.print_topic_times(topic=0) # evolution of 1st topic through all timeslices

[[('learning', 0.025603854114769783),
  ('classification', 0.013078957962035015),
  ('data', 0.012677044212829452),
  ('classifier', 0.011060039338439116),
  ('algorithm', 0.010027359430946065),
  ('method', 0.00988597414722764),
  ('task', 0.009632282635041407),
  ('label', 0.009610704646834571),
  ('loss', 0.00882274877851846),
  ('problem', 0.008643380335888465),
  ('training', 0.008382162521872764),
  ('approach', 0.008163789004139532),
  ('show', 0.007616260947406465),
  ('function', 0.007284996092877158),
  ('prediction', 0.006792233812015062),
  ('set', 0.0066016826398595145),
  ('ranking', 0.006278589759083451),
  ('result', 0.006177324438251663),
  ('performance', 0.005863261368254407),
  ('active', 0.005759523401113835)],
 [('learning', 0.025679855252956428),
  ('classification', 0.013108468533573251),
  ('data', 0.012705873055026087),
  ('classifier', 0.011083703772189016),
  ('algorithm', 0.010047255240349665),
  ('method', 0.0099061631632319),
  ('task', 0.0096517361634171

In [16]:
ldaseq.print_topic_times(topic=1) 

[[('neural', 0.03311428597144948),
  ('network', 0.030222057201737283),
  ('neuron', 0.028473205911846815),
  ('spike', 0.017532654531892743),
  ('activity', 0.01747704911373525),
  ('learning', 0.012382830759507702),
  ('input', 0.011840526532021223),
  ('dynamic', 0.010303424140222565),
  ('signal', 0.010184339395370987),
  ('system', 0.0094180634366487),
  ('population', 0.00909417582282744),
  ('show', 0.007875783915605743),
  ('cell', 0.00773029120356141),
  ('brain', 0.007663786235615744),
  ('spiking', 0.0071239297657165485),
  ('pattern', 0.007052366993056199),
  ('linear', 0.007021868762973844),
  ('rule', 0.006664801490916421),
  ('state', 0.006617620394600872),
  ('response', 0.006279890360587671)],
 [('neural', 0.032891224722349),
  ('network', 0.030068447030895906),
  ('neuron', 0.028637454788320225),
  ('spike', 0.01760920205056897),
  ('activity', 0.01755329200811497),
  ('learning', 0.012419744762579576),
  ('input', 0.011785544899412618),
  ('dynamic', 0.01033659533124

In [17]:
ldaseq.print_topic_times(topic=2) 

[[('image', 0.025159407451535915),
  ('model', 0.01714599467030103),
  ('feature', 0.01628877888276822),
  ('object', 0.013696213179637626),
  ('learning', 0.010168055497688906),
  ('task', 0.009935225286329261),
  ('visual', 0.007864813830819016),
  ('method', 0.007230728548604607),
  ('approach', 0.006948322071761694),
  ('representation', 0.006854114628734229),
  ('training', 0.005960962646856371),
  ('recognition', 0.00573595019014691),
  ('using', 0.00541296637831376),
  ('human', 0.005333428630096084),
  ('performance', 0.0050845769947871905),
  ('show', 0.005010665036933593),
  ('data', 0.0049808318877471855),
  ('network', 0.004911993531397363),
  ('result', 0.004707449662838983),
  ('two', 0.0043237586276344995)],
 [('image', 0.02511044166992057),
  ('model', 0.017198106895957847),
  ('feature', 0.016438364638111623),
  ('object', 0.013737750644520737),
  ('learning', 0.010195354689156562),
  ('task', 0.009996740924476293),
  ('visual', 0.0079055206262468),
  ('method', 0.0072

In [18]:
ldaseq.print_topic_times(topic=3) 

[[('model', 0.04522000972998711),
  ('data', 0.01999694700694506),
  ('method', 0.010415788149254358),
  ('distribution', 0.009300994060369383),
  ('process', 0.009226306875747103),
  ('latent', 0.008616586410013819),
  ('approach', 0.007505025252983424),
  ('bayesian', 0.007254471730031124),
  ('inference', 0.0068918930915970265),
  ('variable', 0.006689709307943255),
  ('structure', 0.0066262244421468105),
  ('using', 0.006240638243278333),
  ('prior', 0.006126252390794715),
  ('based', 0.005066696254985804),
  ('probabilistic', 0.0050526877784106364),
  ('gaussian', 0.004659505310205848),
  ('topic', 0.004638435536627907),
  ('show', 0.004423113791481357),
  ('mixture', 0.004402143231467874),
  ('learning', 0.004389406452313889)],
 [('model', 0.04516686768421443),
  ('data', 0.02008611586041927),
  ('method', 0.010449700666297966),
  ('distribution', 0.00932997906463583),
  ('process', 0.009214592554613635),
  ('latent', 0.008642199668643002),
  ('approach', 0.007525649248277168),
 

In [19]:
ldaseq.print_topic_times(topic=4) 

[[('stimulus', 0.01640738055732014),
  ('regression', 0.01586972318153773),
  ('estimation', 0.014955023763457285),
  ('estimator', 0.014891604044562981),
  ('model', 0.012401279512340279),
  ('information', 0.011651502064563508),
  ('distribution', 0.011317700556806186),
  ('density', 0.009625330875172419),
  ('estimate', 0.009321273568345041),
  ('sample', 0.008717381131189226),
  ('statistical', 0.008119337048746992),
  ('parameter', 0.00759345868044461),
  ('rate', 0.007574848957029941),
  ('response', 0.007482541905117516),
  ('show', 0.007347999649282885),
  ('noise', 0.006383604035494355),
  ('result', 0.006192444904993055),
  ('analysis', 0.006086549999646608),
  ('sensory', 0.005952042426361563),
  ('case', 0.005817264255220472)],
 [('stimulus', 0.016453636742532956),
  ('regression', 0.015914125857846774),
  ('estimation', 0.014995099155873097),
  ('estimator', 0.014931989614997813),
  ('model', 0.012431792012810033),
  ('information', 0.011666225554717115),
  ('distribution'

In [20]:
ldaseq.print_topic_times(topic=5) 

[[('matrix', 0.0737789414606467),
  ('sparse', 0.04333039878468099),
  ('signal', 0.0212708783285884),
  ('algorithm', 0.019969550138450014),
  ('norm', 0.012310750859974405),
  ('covariance', 0.011599715877510016),
  ('measurement', 0.011538412591894849),
  ('pca', 0.011492765634946552),
  ('tensor', 0.010858115220313134),
  ('rank', 0.010611533081560445),
  ('recovery', 0.010609277713352992),
  ('vector', 0.010121579831317997),
  ('lowrank', 0.009822399613446168),
  ('data', 0.009208517943068201),
  ('analysis', 0.008206923846017558),
  ('number', 0.008147406319303614),
  ('factorization', 0.008107601077063506),
  ('dictionary', 0.00808962567913131),
  ('time', 0.007711872892990051),
  ('component', 0.00767353867934632)],
 [('matrix', 0.07428652882819928),
  ('sparse', 0.043544848254039405),
  ('signal', 0.021167968790191925),
  ('algorithm', 0.019883757318722634),
  ('norm', 0.012339222895613488),
  ('covariance', 0.01162516214932006),
  ('measurement', 0.011563634024081683),
  ('pc

In [21]:
ldaseq.print_topic_times(topic=6) 

[[('algorithm', 0.025120138942813678),
  ('problem', 0.020754104182093894),
  ('method', 0.020191719760488138),
  ('learning', 0.013947437693038493),
  ('function', 0.01368538616071467),
  ('kernel', 0.013016674408557546),
  ('data', 0.011510747925113954),
  ('optimization', 0.008395678877291196),
  ('paper', 0.007188470753656931),
  ('show', 0.007148626436996221),
  ('convex', 0.007137199975942383),
  ('linear', 0.006475446211595404),
  ('result', 0.005978254821755761),
  ('approach', 0.0059528404226556015),
  ('convergence', 0.005887255977631561),
  ('based', 0.005498889443235153),
  ('proposed', 0.005427442857398774),
  ('gradient', 0.005220626636692649),
  ('solution', 0.005136364056706335),
  ('regularization', 0.004991029541784632)],
 [('algorithm', 0.025199101515322748),
  ('problem', 0.020816272953423864),
  ('method', 0.02025068418286624),
  ('learning', 0.013983501474469811),
  ('function', 0.013720446442682842),
  ('kernel', 0.0130482888653003),
  ('data', 0.0115374467973039

In [22]:
ldaseq.print_topic_times(topic=7) 

[[('algorithm', 0.031430833335314164),
  ('bound', 0.030717986045851575),
  ('online', 0.01469417932339075),
  ('problem', 0.013539583194879),
  ('regret', 0.011255050194635165),
  ('learning', 0.010860297646176407),
  ('setting', 0.009846589216547042),
  ('complexity', 0.00866766347242031),
  ('show', 0.008514101873466982),
  ('number', 0.006580459352124879),
  ('game', 0.006558517068276738),
  ('result', 0.0065208010552935194),
  ('case', 0.006440868495911511),
  ('sample', 0.006377434633800216),
  ('time', 0.005920452658894243),
  ('distribution', 0.005908275533397656),
  ('lower', 0.005737155664782986),
  ('bandit', 0.005313505886762903),
  ('study', 0.0051170264485049174),
  ('general', 0.005024303040744034)],
 [('algorithm', 0.03153190523174136),
  ('bound', 0.030816487196246654),
  ('online', 0.014730291171509041),
  ('problem', 0.013571888952846679),
  ('regret', 0.011279863969798866),
  ('learning', 0.010883623313853678),
  ('setting', 0.009867080818053969),
  ('complexity', 0

In [23]:
ldaseq.print_topic_times(topic=8) 

[[('algorithm', 0.015805281428896083),
  ('policy', 0.014008362926912108),
  ('problem', 0.011837893685511344),
  ('learning', 0.011623744863604372),
  ('state', 0.010922954757437334),
  ('method', 0.010867655884992049),
  ('inference', 0.010071668781598686),
  ('model', 0.01004806363554277),
  ('approach', 0.009468268509055845),
  ('markov', 0.007762285671351675),
  ('function', 0.007414219908075516),
  ('show', 0.007097089229574044),
  ('process', 0.007013177008684772),
  ('approximation', 0.006467856163445303),
  ('control', 0.0064204072581162),
  ('decision', 0.006170219911049581),
  ('using', 0.00608605502966886),
  ('belief', 0.006067152081438999),
  ('reinforcement', 0.006012403868189768),
  ('sampling', 0.006003534094933431)],
 [('algorithm', 0.015845534581590704),
  ('policy', 0.014042622937355791),
  ('problem', 0.01186440583872779),
  ('learning', 0.011649529585396763),
  ('state', 0.010946691067778798),
  ('method', 0.010892060803587235),
  ('inference', 0.01009277365316413

In [24]:
ldaseq.print_topic_times(topic=9) 

[[('graph', 0.030757940723895132),
  ('algorithm', 0.026068655298834426),
  ('clustering', 0.02143440010001221),
  ('tree', 0.015265785310173882),
  ('network', 0.013013476335436681),
  ('structure', 0.012230305885663092),
  ('problem', 0.01163858738496824),
  ('cluster', 0.010193092170870086),
  ('show', 0.009997898498128741),
  ('random', 0.00940973840756088),
  ('node', 0.008901440062789666),
  ('inference', 0.008716954397751855),
  ('model', 0.008475939274314895),
  ('number', 0.007530659433418215),
  ('large', 0.007426665364721433),
  ('time', 0.006178318247355415),
  ('paper', 0.006130790082935241),
  ('data', 0.0056143997303762135),
  ('set', 0.005503582388607582),
  ('result', 0.0054075691982345495)],
 [('graph', 0.0308589720527307),
  ('algorithm', 0.026149477637234176),
  ('clustering', 0.021496218794146416),
  ('tree', 0.015303651952552141),
  ('network', 0.013039583835884706),
  ('structure', 0.012257855909329183),
  ('problem', 0.011664124815450875),
  ('cluster', 0.010212

In [25]:
# to check Document - Topic proportions, use `doc-topics`
#doc = ldaseq.doc_topics(558) # check the 558th document in the corpuses topic distribution
#print (doc)
# this document is made up of different topics like this

In [26]:
# make a graph by checking the topic proportions and putting them on a graph 
# same with coherence
# do hellingers distance between topics?

In [27]:
ldaseq.print_topic_times(1) # evolution of 2nd topic through all timeslices


[[('neural', 0.03311428597144948),
  ('network', 0.030222057201737283),
  ('neuron', 0.028473205911846815),
  ('spike', 0.017532654531892743),
  ('activity', 0.01747704911373525),
  ('learning', 0.012382830759507702),
  ('input', 0.011840526532021223),
  ('dynamic', 0.010303424140222565),
  ('signal', 0.010184339395370987),
  ('system', 0.0094180634366487),
  ('population', 0.00909417582282744),
  ('show', 0.007875783915605743),
  ('cell', 0.00773029120356141),
  ('brain', 0.007663786235615744),
  ('spiking', 0.0071239297657165485),
  ('pattern', 0.007052366993056199),
  ('linear', 0.007021868762973844),
  ('rule', 0.006664801490916421),
  ('state', 0.006617620394600872),
  ('response', 0.006279890360587671)],
 [('neural', 0.032891224722349),
  ('network', 0.030068447030895906),
  ('neuron', 0.028637454788320225),
  ('spike', 0.01760920205056897),
  ('activity', 0.01755329200811497),
  ('learning', 0.012419744762579576),
  ('input', 0.011785544899412618),
  ('dynamic', 0.01033659533124

In [28]:
from gensim.models.coherencemodel import CoherenceModel

# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=2)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass1", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV1", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=3)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass2", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV2", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=4)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass3", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV3", cm_DTM.get_coherence())




# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=5)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass4", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV4", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=6)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass5", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV5", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=7)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass6", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV6", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=8)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass7", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV7", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=9)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass8", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV8", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=10)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass9", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV9", cm_DTM.get_coherence())




# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=11)
# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass10", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV10", cm_DTM.get_coherence())


# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=12)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass11", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV11", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=13)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass12", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV12", cm_DTM.get_coherence())

U_Mass1 -1.8560584519531425
CV1 0.41252190724159893
U_Mass2 -1.856541634520952
CV2 0.41252190724159893
U_Mass3 -1.8404301537409549
CV3 0.4116869561924827
U_Mass4 -1.861630042963882
CV4 0.4102856458555203
U_Mass5 -1.824342722555047
CV5 0.4137275191265598
U_Mass6 -1.8008620357746605
CV6 0.41421599894731953
U_Mass7 -1.788592626294151
CV7 0.419092704636567
U_Mass8 -1.806352591202169
CV8 0.42176628734834953
U_Mass9 -1.8005709167341095
CV9 0.415261159573597
U_Mass10 -1.8385146486098365
CV10 0.41945461319948923
U_Mass11 -1.862054696835235
CV11 0.4074833324261893
U_Mass12 -1.8687194223871266
CV12 0.40671315350207227


In [32]:
save(ldaseq)

'' was not found in history, as a file, url, nor in the user namespace.


# https://datascience.blog.wzb.eu/2017/11/09/topic-modeling-evaluation-in-python-with-tmtoolkit/